In [2]:
import os
from groq import Groq
import pandas as pd
import numpy as np

In [ ]:
apiKey = "fill_it_here"

In [4]:
client = Groq(
    # api_key=os.environ.get("GROQ_API_KEY"),
    api_key= apiKey,
)

In [5]:
dataset = pd.read_csv("/home/patrick/Downloads/test3label/keyphrases/done/keyphrases_AmazonMixtral_Done.csv")

In [6]:
dataset

Unnamed: 0                                            content  \
0              0          Isn't really worth the price that you pay   
1            549  Charge way to much compared to any other strea...   
2           1052  No point in searching for movies here, its eas...   
3           1159  If Netflix crack down password sharing They si...   
4           2123  Too expensive Cant share a account without people   
...          ...                                                ...   
2695        2649         The app won't work on my Google pixel 8 😩😩   
2696        2680                   It doesn't work on Huawei phone😣   
2697        2650  Replay, absurd movies. Netflix should have mor...   
2698        2663  I hate that it does not want me to download gt...   
2699        2671  STOP TAKING ALL OF THE GOOD MOVIES AWAY JUST T...   

                                    keyphrases_original  cluster  sentiment  \
0     ['Netflix', 'price', 'worth', 'subscription', ...      356          1   
1     ['Netflix price', 'high cost', 'streaming serv...      356          0   
2     ['netflix', 'search', 'movies', 'finding', 'ea...      356          0   
3     ['password sharing', 'netflix', 'platform', 's...      356          1   
4     ['expense', 'price', 'Netflix', 'sharing', 'ac...      356          1   
...                                                 ...      ...        ...   
2695  ['google pixel 8 issues', 'netflix app problem...      182          0   
2696  ['Netflix app error', 'Huawei phone issue', 'c...      182          0   
2697  ['netflix', 'replay', 'movies', 'new movies', ...      260          0   
2698  ['Netflix App Error', 'No Download Option', 'G...      292          0   
2699  ['netflix movies', 'good movies', 'big mouth',...      498          0   

      count                                 keyphrases_reduced  \
0         6  ['Netflix price', 'expensive streaming service...   
1         6  ['Netflix price', 'expensive streaming service...   
2         6  ['Netflix price', 'expensive streaming service...   
3         6  ['Netflix price', 'expensive streaming service...   
4         6  ['Netflix price', 'expensive streaming service...   
...     ...                                                ...   
2695      2  ['Google Pixel 8 Netflix app issues', 'Android...   
2696      2  ['Google Pixel 8 Netflix app issues', 'Android...   
2697      1  ['netflix', 'replay', 'movies', 'new movies', ...   
2698      1  ['Netflix App Error', 'No Download Option', 'G...   
2699      1  ['netflix movies', 'good movies', 'big mouth',...   

                              Merged keyphrases_reduced  \
0     ['Netflix price', 'expensive streaming service...   
1     ['Netflix price', 'expensive streaming service...   
2     ['Netflix price', 'expensive streaming service...   
3     ['Netflix price', 'expensive streaming service...   
4     ['Netflix price', 'expensive streaming service...   
...                                                 ...   
2695  ['Google Pixel 8 Netflix app issues', 'Android...   
2696  ['Google Pixel 8 Netflix app issues', 'Android...   
2697  ['netflix', 'replay', 'movies', 'new movies', ...   
2698  ['payment issue', 'compatibility problem', 'in...   
2699  ['payment issue', 'compatibility problem', 'in...   

      count merged keyphrases_reduced kw newly generated  id Mkr  \
0                                   6                NaN       0   
1                                   6                NaN       0   
2                                   6                NaN       0   
3                                   6                NaN       0   
4                                   6                NaN       0   
...                               ...                ...     ...   
2695                                2                NaN     425   
2696                                2                NaN     425   
2697                                1                NaN     426   
2698                  

In [7]:
score_counts_balanced = dataset['sentiment'].value_counts().sort_index()
print(score_counts_balanced)

sentiment
0    900
1    900
2    900
Name: count, dtype: int64


In [8]:
train_data = dataset[['content', 'sentiment', 'Merged keyphrases_reduced 2']]
train_data['row_number'] = train_data.index

/tmp/ipykernel_1736365/1289041381.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_data['row_number'] = train_data.index


In [9]:
train_data

content  sentiment  \
0             Isn't really worth the price that you pay          1   
1     Charge way to much compared to any other strea...          0   
2     No point in searching for movies here, its eas...          0   
3     If Netflix crack down password sharing They si...          1   
4     Too expensive Cant share a account without people          1   
...                                                 ...        ...   
2695         The app won't work on my Google pixel 8 😩😩          0   
2696                   It doesn't work on Huawei phone😣          0   
2697  Replay, absurd movies. Netflix should have mor...          0   
2698  I hate that it does not want me to download gt...          0   
2699  STOP TAKING ALL OF THE GOOD MOVIES AWAY JUST T...          0   

                            Merged keyphrases_reduced 2  row_number  
0     ['Netflix price', 'expensive streaming service...           0  
1     ['Netflix price', 'expensive streaming service...           1  
2     ['Netflix price', 'expensive streaming service...           2  
3     ['Netflix price', 'expensive streaming service...           3  
4     ['Netflix price', 'expensive streaming service...           4  
...                                                 ...         ...  
2695  ['Google Pixel 8 Netflix app issues', 'Android...        2695  
2696  ['Google Pixel 8 Netflix app issues', 'Android...        2696  
2697  ['Netflix pricing', 'Expensive subscription', ...        2697  
2698  ['Watch a movie', 'New Shows', 'Movies', 'Sitc...        2698  
2699  ['Watch a movie', 'New Shows', 'Movies', 'Sitc...        2699  

[2700 rows x 4 columns]

In [10]:
list = []
i = 0
for index, row in train_data.iterrows():
    text = row['content']
    topics = row['Merged keyphrases_reduced 2']
    string_message = f"""I need you to evaluate and assess the comment along with the set of topics/keyphrases, categorizing their sentiment into one of five levels: 1 - negative, 2 - neutral, or 3 - positive. Here are examples to guide your classification:

                1. Comment: "Sluggish app, also fails to open links from Google searches. App is set to open all Amazon links. Tried clearing cache, data, uninstalling, reinstalling. Nothing improves."
                Topics / Keyphrases: ['Amazon App issues', 'timing out regularly', 'ERR_TIMED_OUT error', 'user frustration', 'sluggish performance', 'Google Play Store links', 'data cleaning', 'uninstalling-reinstalling app', 'phone application loading issue', 'persistent lock-up problem']
                Label: 1
                
                2. Comment: "Delivery is always on point and this app is great, but my only issue is that the screen keeps on freezing, I can barely use it. Overall, nice job."
                Topics / Keyphrases: ['User Experience', 'Shopping', 'Item Returns', 'Country Change', 'Prime Membership', 'Payment Issues', 'Location Settings', 'Delivery Speed Comparison', 'Design Issue', 'User Sentiment']
                Label: 2
                
                3. Comment: "it's great to have when I think of something I wat or need. it's right in front of me to open before I Foret what's on list."
                Topics / Keyphrases: ['Amazon App', 'User Experience', 'Shopping', 'Location Settings', 'Google Play Store', 'Item Returns', 'Country Change', 'Prime Membership', 'Rating', 'Recommendation']
                Label: 3
                
                Please provide the sentiment classification as a single number (1, 2, or 3) and nothing more for the following comment:

                Comment: "{text}"
                Topics / Keyphrases: {topics}
                Label: ?
                """
    print("\n\n")
    print(string_message)
    print("\n")
    
    chat_completion = client.chat.completions.create(
        messages = [
            {
                "role": "user",
                "content": f"""{string_message}"""
            }
    
        ],
        # model="llama3-8b-8192",
        model="mixtral-8x7b-32768",
    )

    armaz = chat_completion.choices[0].message.content
    print(f'{index}:\t{armaz}')
    list.append(armaz)




I need you to evaluate and assess the comment along with the set of topics/keyphrases, categorizing their sentiment into one of five levels: 1 - negative, 2 - neutral, or 3 - positive. Here are examples to guide your classification:

                1. Comment: "i am not enjoying it in chromebook the scrolling feels sucks the app needs more atention in chromebooks even thoug the audio and quality feels sucks in chrome book even though i am using google pixel book it needs to be optimized for chromebooks"
                Topics / Keyphrases: ['Netflix App Issues', 'Android Device Problem', 'Video Playback Problem', 'Streaming Issue', 'App Crash', 'Video Buffering', 'Loading Problem', 'Audio Quality Problem', 'Device Compatibility Problem', 'App Optimization Issue']
                Label: 1
                
                2. Comment: "Good overall but definitely room for improvement especially in relation to multitasking. The Netflix app totally cuts out any ability to multitask this

APITimeoutError: Request timed out.

In [13]:
len(list)

1651

In [14]:
rest = train_data[len(list):]
for index, row in rest.iterrows():
    text = row['content']
    topics = row['Merged keyphrases_reduced 2']
    string_message = f"""I need you to evaluate and assess the comment along with the set of topics/keyphrases, categorizing their sentiment into one of five levels: 1 - negative, 2 - neutral, or 3 - positive. Here are examples to guide your classification:

                1. Comment: "Sluggish app, also fails to open links from Google searches. App is set to open all Amazon links. Tried clearing cache, data, uninstalling, reinstalling. Nothing improves."
                Topics / Keyphrases: ['Amazon App issues', 'timing out regularly', 'ERR_TIMED_OUT error', 'user frustration', 'sluggish performance', 'Google Play Store links', 'data cleaning', 'uninstalling-reinstalling app', 'phone application loading issue', 'persistent lock-up problem']
                Label: 1
                
                2. Comment: "Delivery is always on point and this app is great, but my only issue is that the screen keeps on freezing, I can barely use it. Overall, nice job."
                Topics / Keyphrases: ['User Experience', 'Shopping', 'Item Returns', 'Country Change', 'Prime Membership', 'Payment Issues', 'Location Settings', 'Delivery Speed Comparison', 'Design Issue', 'User Sentiment']
                Label: 2
                
                3. Comment: "it's great to have when I think of something I wat or need. it's right in front of me to open before I Foret what's on list."
                Topics / Keyphrases: ['Amazon App', 'User Experience', 'Shopping', 'Location Settings', 'Google Play Store', 'Item Returns', 'Country Change', 'Prime Membership', 'Rating', 'Recommendation']
                Label: 3
                
                Please provide the sentiment classification as a single number (1, 2, or 3) and nothing more for the following comment:

                Comment: "{text}"
                Topics / Keyphrases: {topics}
                Label: ?
                """
    print("\n\n")
    print(string_message)
    print("\n")
    
    chat_completion = client.chat.completions.create(
        messages = [
            {
                "role": "user",
                "content": f"""{string_message}"""
            }
    
        ],
        # model="llama3-8b-8192",
        model="mixtral-8x7b-32768",
    )

    armaz = chat_completion.choices[0].message.content
    print(f'{index}:\t{armaz}')
    list.append(armaz)




I need you to evaluate and assess the comment along with the set of topics/keyphrases, categorizing their sentiment into one of five levels: 1 - negative, 2 - neutral, or 3 - positive. Here are examples to guide your classification:

                1. Comment: "i am not enjoying it in chromebook the scrolling feels sucks the app needs more atention in chromebooks even thoug the audio and quality feels sucks in chrome book even though i am using google pixel book it needs to be optimized for chromebooks"
                Topics / Keyphrases: ['Netflix App Issues', 'Android Device Problem', 'Video Playback Problem', 'Streaming Issue', 'App Crash', 'Video Buffering', 'Loading Problem', 'Audio Quality Problem', 'Device Compatibility Problem', 'App Optimization Issue']
                Label: 1
                
                2. Comment: "Good overall but definitely room for improvement especially in relation to multitasking. The Netflix app totally cuts out any ability to multitask this

In [16]:
len(list)

2700

In [20]:
train_data['predictedSentiment'] = list

/tmp/ipykernel_1736365/858559427.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_data['predictedSentiment'] = list


In [21]:
import re
def findNumbers(string):
    # Find all numbers in the string
    numbers = re.findall(r'\d+', string)
    
    # Convert the numbers to integers
    numbers = [int(x) for x in numbers]
    
    if(len(numbers)>0):
        x = numbers[0]-1
    else:
        x = -1
    return x

In [22]:
formated = train_data['predictedSentiment'].apply(findNumbers)

In [23]:
train_data['predictedSentiment'] = formated

/tmp/ipykernel_1736365/188460712.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_data['predictedSentiment'] = formated


In [24]:
train_data

content  sentiment  \
0             Isn't really worth the price that you pay          1   
1     Charge way to much compared to any other strea...          0   
2     No point in searching for movies here, its eas...          0   
3     If Netflix crack down password sharing They si...          1   
4     Too expensive Cant share a account without people          1   
...                                                 ...        ...   
2695         The app won't work on my Google pixel 8 😩😩          0   
2696                   It doesn't work on Huawei phone😣          0   
2697  Replay, absurd movies. Netflix should have mor...          0   
2698  I hate that it does not want me to download gt...          0   
2699  STOP TAKING ALL OF THE GOOD MOVIES AWAY JUST T...          0   

                            Merged keyphrases_reduced 2  row_number  \
0     ['Netflix price', 'expensive streaming service...           0   
1     ['Netflix price', 'expensive streaming service...           1   
2     ['Netflix price', 'expensive streaming service...           2   
3     ['Netflix price', 'expensive streaming service...           3   
4     ['Netflix price', 'expensive streaming service...           4   
...                                                 ...         ...   
2695  ['Google Pixel 8 Netflix app issues', 'Android...        2695   
2696  ['Google Pixel 8 Netflix app issues', 'Android...        2696   
2697  ['Netflix pricing', 'Expensive subscription', ...        2697   
2698  ['Watch a movie', 'New Shows', 'Movies', 'Sitc...        2698   
2699  ['Watch a movie', 'New Shows', 'Movies', 'Sitc...        2699   

      predictedSentiment  
0                      0  
1                      0  
2                      0  
3                      0  
4                      0  
...                  ...  
2695                   0  
2696                   0  
2697                   0  
2698                   0  
2699                   0  

[2700 rows x 5 columns]

In [25]:
train_data.to_csv('/home/patrick/Downloads/test3label/mixtralOutput/topics/filenameAmazonOneShotMixtral-T.csv', index=False)

In [112]:
results = pd.read_csv("/home/patrick/Downloads/test3label/mixtralOutput/topics/filenameAmazonOneShotMixtral-T.csv")

In [113]:
results

content  scoreSA  \
0     This company supports zionism and funds childr...        0   
1             Supporting terrorism and killing children        2   
2       They support Isr@il. Boycotting Amazon for life        0   
3                   This company is supporting genocide        4   
4     Uninstall this app because his support for the...        2   
...                                                 ...      ...   
2495  Everything is on time . Damaged products rarel...        0   
2496  Good app but it is not available in my country...        3   
2497  If you sort by low-to-high, it removes 80% of ...        1   
2498  Now zero stars..cancel prime..Amazon keeps dev...        2   
2499  COD is not working, it only gives you a fracti...        0   

                            Merged keyphrases_reduced 2  row_number  \
0     ['Amazon App', 'Google Play Store', 'user opin...           0   
1     ['Amazon App', 'Google Play Store', 'user opin...           1   
2     ['Amazon App', 'Google Play Store', 'user opin...           2   
3     ['Amazon App', 'Google Play Store', 'user opin...           3   
4     ['Amazon App', 'Google Play Store', 'user opin...           4   
...                                                 ...         ...   
2495  ['Amazon Prime', 'online shopping', 'product d...        2495   
2496  ['Amazon App', 'user experience', 'Google Play...        2496   
2497  ['Amazon App', 'user experience', 'Google Play...        2497   
2498  ['Amazon Prime', 'online shopping', 'product d...        2498   
2499  ['Amazon App', 'user experience', 'Google Play...        2499   

      predictedSentiment  
0                      0  
1                      0  
2                      0  
3                      0  
4                      0  
...                  ...  
2495                   4  
2496                   1  
2497                   1  
2498                   1  
2499                   1  

[2500 rows x 5 columns]

In [114]:
results['predictedSentiment'].value_counts().sort_index()

predictedSentiment
0     359
1    1272
2     188
3     256
4     425
Name: count, dtype: int64

In [115]:
filtered_df = results[results["predictedSentiment"] == -1]

In [116]:
filtered_df

Empty DataFrame
Columns: [content, scoreSA, Merged keyphrases_reduced 2, row_number, predictedSentiment]
Index: []

In [117]:
newResults = results[results["predictedSentiment"] != -1]

In [ ]:
newResults

In [119]:
from matplotlib.ticker import PercentFormatter
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import confusion_matrix

def cm_analysis(y_true, y_pred, filename, labels, classes, ymap=None, figsize=(17,17)):
    """
    Generate matrix plot of confusion matrix with pretty annotations.
    The plot image is saved to disk.
    args: 
      y_true:    true label of the data, with shape (nsamples,)
      y_pred:    prediction of the data, with shape (nsamples,)
      filename:  filename of figure file to save
      labels:    string array, name the order of class labels in the confusion matrix.
                 use `clf.classes_` if using scikit-learn models.
                 with shape (nclass,).
      classes:   aliases for the labels. String array to be shown in the cm plot.
      ymap:      dict: any -> string, length == nclass.
                 if not None, map the labels & ys to more understandable strings.
                 Caution: original y_true, y_pred and labels must align.
      figsize:   the size of the figure plotted.
    """
    sns.set(font_scale=2.8)

    if ymap is not None:
        y_pred = [ymap[yi] for yi in y_pred]
        y_true = [ymap[yi] for yi in y_true]
        labels = [ymap[yi] for yi in labels]
    cm = confusion_matrix(y_true, y_pred, labels=labels)
    cm_sum = np.sum(cm, axis=1, keepdims=True)
    cm_perc = cm / cm_sum.astype(float) * 100
    annot = np.empty_like(cm).astype(str)
    nrows, ncols = cm.shape
    for i in range(nrows):
        for j in range(ncols):
            c = cm[i, j]
            p = cm_perc[i, j]
            if i == j:
                s = cm_sum[i]
                annot[i, j] = '%.2f%%\n%d/%d' % (p, c, s)
            #elif c == 0:
            #    annot[i, j] = ''
            else:
                annot[i, j] = '%.2f%%\n%d' % (p, c)
    cm = confusion_matrix(y_true, y_pred, labels=labels, normalize='true')
    cm = pd.DataFrame(cm, index=labels, columns=labels)
    cm = cm * 100
    cm.index.name = 'True Label'
    cm.columns.name = 'Predicted Label'
    fig, ax = plt.subplots(figsize=figsize)
    plt.yticks(va='center')

    sns.heatmap(cm, annot=annot, fmt='', ax=ax, xticklabels=classes, cbar=True, cbar_kws={'format':PercentFormatter()}, yticklabels=classes, cmap="Blues")
    plt.savefig(f'{filename}.png',  bbox_inches='tight')
    plt.savefig(f'{filename}.svg',  bbox_inches='tight')

In [120]:
# Generate the confusion matrix
unique_labels = np.sort(newResults['scoreSA'].unique())
mapping = {0: 'Very Negative (1)', 1: 'Negative (2)', 2: 'Neutral (3)', 3: 'Positive (4)', 4: 'Very Positive (5)'}

# Applying mapping
classes = [mapping[value] for value in unique_labels]

In [ ]:
cm_analysis(newResults['scoreSA'], newResults['predictedSentiment'], 'API', unique_labels, classes)

In [122]:
from sklearn.metrics import accuracy_score, balanced_accuracy_score, precision_score, recall_score, f1_score, precision_recall_fscore_support, mean_absolute_error

accuracy = accuracy_score(newResults['scoreSA'], newResults['predictedSentiment'])
precision_ALL = precision_score(newResults['scoreSA'], newResults['predictedSentiment'], average='macro')
recall_ALL = recall_score(newResults['scoreSA'], newResults['predictedSentiment'], average='macro')
f1_ALL = f1_score(newResults['scoreSA'], newResults['predictedSentiment'], average='macro')
mae_ALL = mean_absolute_error(newResults['scoreSA'], newResults['predictedSentiment'])
precision, recall, f1, support = precision_recall_fscore_support(newResults['scoreSA'], newResults['predictedSentiment'])

In [ ]:
# Calculate accuracy for each class
for i in range(len(unique_labels)):
    temp = newResults[newResults["scoreSA"] == i]
    value = accuracy_score(temp['scoreSA'], temp['predictedSentiment'])
    print(f'Label:\t{i}\t-\tValue:\t{value}')

In [ ]:
accuracy

In [125]:
balanced_accuracy = balanced_accuracy_score(results['scoreSA'], results['predictedSentiment'])

In [ ]:
balanced_accuracy

In [ ]:
precision_ALL

In [128]:
recall_ALL

0.1888

In [ ]:
f1_ALL

In [ ]:
mae_ALL

In [ ]:
precision

In [ ]:
recall

In [ ]:
f1

In [ ]:
support